# 🧬 Training a discrete diffusion model on biological sequences

This notebook demonstrates how to **fine-tune NTv3** for controllable enhancer sequence generation using **Masked Diffusion Language Modeling (MDLM)** ([paper](https://arxiv.org/pdf/2406.07524)).

---

## 🎯 What You'll Learn

This tutorial covers:
1. How to extend a post-trained NTv3 model with new conditioning signals
2. The fundamentals of Masked Diffusion Language Modeling (MDLM) for DNA generation
3. Best practices for training generative DNA models with EMA stabilization

---

## 🧪 Background: Generative DNA Modeling

### What is MDLM?

**Masked Diffusion Language Modeling (MDLM)** is a diffusion-based approach adapted for discrete sequences. Unlike continuous diffusion models that add Gaussian noise, MDLM progressively masks tokens:

- **Forward process**: Gradually replace tokens with `[MASK]` according to a noise schedule
- **Reverse process**: Model learns to predict original tokens from masked sequences
- **Sampling**: Start from fully masked sequence and iteratively unmask

This approach combines the strengths of diffusion models (iterative refinement, stable training) with the discrete nature of DNA sequences.

### Why Conditional Generation?

We want to generate enhancer sequences with **specific properties**:
- **Species**: Maintain species-specific sequence patterns (e.g., codon usage, regulatory motifs)
- **Activity level**: Control how "strong" the enhancer should be (low → high activity)
- **Sequence context**: Provided by the input sequences, allow the enhancer design to consider promoter-enhancer interaction.

By conditioning on these attributes, we can generate enhancers that are both biologically realistic and functionally targeted.

---

## 📊 Overview

We fine-tune **NTv3_650M_post** to generate enhancer sequences conditioned on:

| Condition | Source | Training |
|-----------|--------|----------|
| **Species** | Pre-trained embeddings | Frozen (transfer learning) |
| **Activity Level** | New embeddings (bins 0-4) | Trainable |

The training uses MDLM-style diffusion with:
- **Linear noise schedule** for sequence masking (uniform sampling of noise levels)
- **Classifier-free guidance** through activity dropout (10% of samples)
- **Exponential Moving Average (EMA)** for stable inference

---

## 📚 Notebook Structure

1. **Setup**: Load data and base model from HuggingFace
2. **Model Architecture**: Add activity conditioning to NTv3
3. **Training Components**: MDLM masking, loss functions, EMA
4. **Training Loop**: Full training pipeline with LR scheduling
5. **Dataset**: Prepare enhancer sequences with activity labels
6. **Run Training**: Execute training on enhancer dataset

---

## 💻 Hardware Requirements
In order to train the 650M parameter model, we recommend using a GPU with at least 40GB of memory, such as the NVIDIA A100.
The hyperparameters in this notebook is set to run a full training that's expected to take around 80hr on a single GPU. 


> 📝 **Note for Google Colab users:** This notebook is compatible with Colab! Enable GPU for faster training: Runtime → Change runtime type → GPU.
> However, due to memory limit, the full scale training for the 650M model needs to be ran with A100 or better GPUs.

## 0) 📦 Setup

First, we import the required libraries and authenticate with HuggingFace to access the pre-trained model and dataset.

### Dependencies

| Library | Purpose |
|---------|---------|
| `torch` | Deep learning framework |
| `transformers` | Load pre-trained NTv3 model and tokenizer |
| `datasets` | Load enhancer generation dataset from HuggingFace |
| `huggingface_hub` | Authentication for gated models |

In [ ]:
import copy
from typing import Any, Dict, List, Optional, Tuple

import numpy as np
import torch
import torch.nn as nn
import torch.nn.functional as F
from datasets import load_dataset
from huggingface_hub import login
from torch.optim import AdamW
from torch.optim.lr_scheduler import LambdaLR
from torch.utils.data import DataLoader, Dataset
from tqdm import tqdm
from transformers import AutoConfig, AutoModel, AutoTokenizer, PreTrainedTokenizer

login()  # Authenticate with HuggingFace

In [ ]:
# Load training dataset and base model
dataset = load_dataset("InstaDeepAI/NTv3_enhancer_generation", split='train')
print(f"Dataset size: {len(dataset)} samples")

model_repo = "InstaDeepAI/NTv3_650M_post"
ntv3_base = AutoModel.from_pretrained(model_repo, trust_remote_code=True)
tokenizer = AutoTokenizer.from_pretrained(model_repo, trust_remote_code=True)
print(f"Base model loaded from {model_repo}")

### 📊 Understanding the Training Data

The dataset `InstaDeepAI/NTv3_enhancer_generation` contains synthetic enhancer sequences with measured activity levels from STARR-seq experiments:

| Field | Description |
|-------|-------------|
| `full_sequence` | Complete construct sequence (promoter + enhancer + reporter) |
| `discrete_label` | Activity bin (0-4): 0 = low activity, 4 = high activity |
| `promoter` | Promoter type used (DSCP or RpS12) |

**Why Activity Bins?**  
Continuous activity values are discretized into 5 bins for conditioning. This makes the conditioning signal more robust and enables discrete classifier-free guidance during generation.

**Enhancer Region Masking**  
During training, we only mask the enhancer region (not the promoter/reporter), as this is the region we want the model to learn to generate. The promoter context is provided as input but not predicted.

---

## 1) 🏗️ Model Architecture

### How NTv3 Conditioning Works

NTv3 supports **discrete conditioning** through learned embedding tables. For each condition:
1. An embedding table maps condition values (e.g., species ID, activity bin) to vectors
2. These vectors modulate the model's hidden states via adaptive layer norm layers
3. A prediction head can optionally predict the condition from the sequence

### Extending with New Conditions

We extend the pre-trained model by adding a **new activity condition**:
- **Species** (index 0): Uses pre-trained embeddings → **frozen**
- **Activity** (index 1): New embeddings initialized randomly → **trainable**

This approach leverages transfer learning: the model retains its species-specific knowledge while learning the new activity conditioning from scratch.


In [3]:
# Configure model with activity conditioning
# - conditions_names[0] = 'species' (frozen, from post-training)
# - conditions_names[1] = 'activity' (trainable, 5 bins)

generation_config = AutoConfig.from_pretrained(
    model_repo,
    conditions_names=['species', 'activity'],
    conditions_vocab_size=[30, 5],  # 30 species, 5 activity bins
    conditions_dims=[16, 16],
    bigwigs_per_species={},
    bed_elements_names=[],
    trust_remote_code=True
)


class GenerativeNTv3(nn.Module):
    """NTv3 model with additional activity conditioning for generation."""

    def __init__(self, config: AutoConfig, base_model: AutoModel):
        super().__init__()
        self.config = config
        # Get the conditioned model class from the base model
        discrete_conditioned_model = type(base_model.core).__bases__[0]
        self.core = discrete_conditioned_model(config)
        # Load pre-trained weights (strict=False allows new conditioning layers)
        self.load_state_dict(base_model.state_dict(), strict=False)

    def forward(
        self,
        input_ids: torch.LongTensor = None,
        condition_ids: List[torch.Tensor] = None,
        conditions_masks: List[torch.Tensor] = None,
        inputs_embeds: torch.FloatTensor = None,
        output_hidden_states: bool = False,
        output_attentions: bool = False,
    ):
        return self.core(
            input_ids=input_ids,
            condition_ids=condition_ids,
            conditions_masks=conditions_masks,
            inputs_embeds=inputs_embeds,
            output_hidden_states=output_hidden_states,
            output_attentions=output_attentions
        )

In [4]:
# Instantiate generative model and freeze species conditioning
generation_model = GenerativeNTv3(generation_config, ntv3_base)
del ntv3_base  # Free memory

# Freeze species conditioning layers (index 0) - only train activity (index 1)
for name, param in generation_model.named_parameters():
    if any(x in name for x in ['modulation_layers.0', 'cond_tables.0', 'conditions_heads.0']):
        param.requires_grad = False

trainable_params = sum(p.numel() for p in generation_model.parameters() if p.requires_grad)
total_params = sum(p.numel() for p in generation_model.parameters())
print(f"Trainable parameters: {trainable_params:,} / {total_params:,} ({100*trainable_params/total_params:.1f}%)")

Trainable parameters: 655,231,760 / 658,672,910 (99.5%)


## 2) 🔧 Training Components

This section defines the core training components for MDLM training.

---

### MDLM Training Strategy

The model is trained to predict masked tokens using:

| Component | Strategy |
|-----------|----------|
| **Sequence loss** | MDLM-style masking with linear noise schedule, weighted CE loss |
| **Activity loss** | Dropout-style masking (10%), CE loss on masked samples only |
| **Species** | Frozen (input conditioning only, no loss) |

> 💡 **Key insight:** Activity is masked during training so the model learns to predict it from the sequence, also enabling classifier-free guidance at inference. However the species logits were never trained and therefore should not be used

---

### The Noise Schedule

In MDLM, the **noise level** $t \in (0, 1]$ determines what fraction of tokens to mask:
- $t = 0$: No masking (original sequence)
- $t = 1$: All tokens masked

During training, we sample $t$ uniformly for each sequence. The loss is weighted by $1/t$ (MDLM weighting) to account for the varying difficulty of different noise levels.

### Classifier-Free Guidance (CFG)

To enable CFG at inference time, we need the model to work both **with** and **without** the activity condition:
- During training: Randomly drop the activity condition with 10% probability
- The model learns: $P(\text{sequence})$ and $P(\text{sequence} | \text{activity})$
- At inference: Use both predictions to amplify the conditioning signal

---

### Masking Function

The `mask_by_noise_level` function implements the forward diffusion process:

In [5]:
def mask_by_noise_level(
    tokens: torch.Tensor,
    noise_level: torch.Tensor,
    mask_token_id: int,
    pad_token_id: int,
    mask_vector: Optional[torch.Tensor] = None,
) -> Tuple[torch.Tensor, torch.Tensor]:
    """
    Mask tokens with probability = noise_level (MDLM diffusion-style).

    Returns:
        masked_tokens: (B, L) with some tokens replaced by mask_token_id
        targets: (B, L) original tokens where masked, pad_token_id elsewhere
    """
    B, L = tokens.shape

    # Mask each position with probability = noise_level
    mask = torch.rand(B, L, device=tokens.device) < noise_level.view(-1, 1)
    mask = mask & (tokens != pad_token_id)  # Don't mask padding

    # Only mask positions specified by mask_vector (if provided)
    if mask_vector is not None:
        mask = mask & mask_vector

    masked_tokens = torch.where(mask, mask_token_id, tokens)
    targets = torch.where(mask, tokens, pad_token_id)
    return masked_tokens, targets


def compute_sequence_loss(
    logits: torch.Tensor,
    targets: torch.Tensor,
    weights: torch.Tensor,
    pad_token_id: int,
    input_tokens: torch.Tensor,
) -> torch.Tensor:
    """MDLM weighted cross-entropy loss, normalized by all non-padding tokens."""
    B, L, V = logits.shape
    sequence_mask = targets != pad_token_id
    loss_denominator_mask = input_tokens != pad_token_id

    ce = F.cross_entropy(
        logits.view(-1, V),
        targets.view(-1),
        reduction='none',
        ignore_index=pad_token_id
    ).view(B, L)

    weighted_ce = ce * weights.unsqueeze(1)
    running_sum_loss = (weighted_ce * sequence_mask).sum(dim=1)
    per_sample_loss = running_sum_loss / loss_denominator_mask.sum(dim=1).clamp(min=1)
    return per_sample_loss.mean()


def compute_activity_loss(
    logits: torch.Tensor,
    targets: torch.Tensor,
    mask: torch.Tensor,
) -> torch.Tensor:
    """Cross-entropy loss for activity prediction (only on masked samples)."""
    if not mask.any():
        return torch.tensor(0.0, device=logits.device)
    return F.cross_entropy(logits[mask], targets[mask])

### Exponential Moving Average (EMA)

EMA maintains a smoothed version of model weights throughout training:

$$\theta_{\text{EMA}} = \beta \cdot \theta_{\text{EMA}} + (1 - \beta) \cdot \theta_{\text{current}}$$

where $\beta = 0.999$ (decay rate).

**Why use EMA for generation?**
- Training weights can be noisy due to stochastic gradient descent
- EMA provides a "averaged" model that's more stable for inference
- Particularly important for generative models where output quality matters
- Adpated from existing literature

At inference time, we use the **EMA model** instead of the training model. This has large impact on the sequence generation quality.

In [6]:
class EMAModel:
    """
    Exponential Moving Average of model parameters.
    Formula: ema_param = decay * ema_param + (1 - decay) * current_param
    """

    def __init__(self, model: nn.Module, decay: float = 0.999):
        self.decay = decay
        self.ema_model = copy.deepcopy(model)
        self.ema_model.eval()
        for param in self.ema_model.parameters():
            param.requires_grad = False

    @torch.no_grad()
    def update(self, model: nn.Module):
        """Update EMA parameters after each training step."""
        for ema_param, model_param in zip(self.ema_model.parameters(), model.parameters()):
            ema_param.data.mul_(self.decay).add_(model_param.data, alpha=1.0 - self.decay)

    def get_model(self) -> nn.Module:
        return self.ema_model

    def state_dict(self) -> Dict[str, Any]:
        return self.ema_model.state_dict()

    def load_state_dict(self, state_dict: Dict[str, Any]):
        self.ema_model.load_state_dict(state_dict)

### Training Step

The `train_step` function implements a single MDLM training iteration:

1. **Sample noise level**: Random $t \sim \text{Uniform}(\epsilon, 1)$ for each sequence
2. **Mask tokens**: Replace tokens with `[MASK]` with probability $t$
3. **Apply condition dropout**: Mask activity with 10% probability (for CFG)
4. **Forward pass**: Model predicts original tokens and activity
5. **Compute losses**: Weighted sequence loss + activity prediction loss
6. **Track metrics**: Accuracy for both sequence and activity predictions

In [7]:
def train_step(
    model: nn.Module,
    tokens: torch.Tensor,
    activity: torch.Tensor,
    species_ids: torch.Tensor,
    mask_vector: Optional[torch.Tensor],
    mask_token_id: int,
    pad_token_id: int,
    activity_masking_prob: float = 0.1,
    activity_loss_weight: float = 1.0,
) -> Dict[str, Any]:
    """Single MDLM training step with sequence and activity losses."""
    B = tokens.shape[0]
    device = tokens.device

    # 1. Sample noise level (linear schedule, avoid t=0 for stability)
    eps = 0.001
    t = torch.rand(B, device=device) * (1 - eps) + eps
    seq_weights = (1.0 / t).clamp(max=100.0)  # MDLM weight = 1/t

    # 2. Mask sequence tokens
    masked_tokens, seq_targets = mask_by_noise_level(
        tokens, t, mask_token_id, pad_token_id, mask_vector
    )

    # 3. Condition masking (dropout for classifier-free guidance)
    species_mask = torch.ones(B, dtype=torch.bool, device=device)  # Always use species
    activity_mask = torch.rand(B, device=device) >= activity_masking_prob  # 10% dropout

    # 4. Forward pass
    outputs = model(
        input_ids=masked_tokens,
        condition_ids=[species_ids, activity],  # Fixed: was conditions_ids
        conditions_masks=[species_mask, activity_mask]
    )

    # 5. Compute losses
    seq_loss = compute_sequence_loss(
        outputs['logits'], seq_targets, seq_weights, pad_token_id, tokens
    )
    activity_loss = compute_activity_loss(
        outputs['condition_1_logits'], activity, ~activity_mask
    )
    total_loss = seq_loss + activity_loss_weight * activity_loss

    # 6. Compute metrics
    seq_mask = seq_targets != pad_token_id
    masked_tokens_count = seq_mask.sum().item()
    total_tokens_count = (tokens != pad_token_id).sum().item()
    masked_activity_count = (~activity_mask).sum().item()

    with torch.no_grad():
        seq_preds = outputs['logits'].argmax(dim=-1)
        seq_correct = (seq_preds == seq_targets) & seq_mask
        seq_accuracy = seq_correct.sum().item() / max(1, masked_tokens_count)

        if masked_activity_count > 0:
            act_preds = outputs['condition_1_logits'].argmax(dim=-1)
            act_correct = (act_preds == activity) & (~activity_mask)
            act_accuracy = act_correct.sum().item() / masked_activity_count
        else:
            act_accuracy = 0.0

    return {
        'loss': total_loss,
        'seq_loss': seq_loss.item(),
        'activity_loss': activity_loss.item(),
        'seq_accuracy': seq_accuracy,
        'act_accuracy': act_accuracy,
        'masked_tokens': masked_tokens_count,
        'total_tokens': total_tokens_count,
        'masked_activity': masked_activity_count,
        'batch_size': B,
    }

## 3) 🔄 Training Loop

This section implements the main training loop with learning rate scheduling.

---

### Learning Rate Schedule

We use a **modified square-root decay** schedule with linear warmup:

1. **Warmup phase**: Linear increase from `initial_lr` to `peak_lr`
2. **Decay phase**: Power-law decay: $\text{LR}(t) = \text{peak\_lr} \times \left(\frac{\text{warmup\_steps}}{t}\right)^\alpha$

This schedule provides:
- Stable early training (warmup prevents large initial updates)
- Gradual refinement (decay allows fine-tuning without overshooting)

### Training Configuration

| Parameter | Recommended Value | Description |
|-----------|------------------|-------------|
| `num_steps` | 500,000+ | Dataset dependent convergence time |
| `lr` | 1e-4 | Peak learning rate |
| `warmup_steps` | 25,000 | ~5% of total steps |
| `ema_decay` | 0.999 | Higher = smoother EMA |
| `activity_masking_prob` | 0.1 | Activity conditioning dropout rate |

In [8]:
def get_modified_sqrt_decay_scheduler(
    optimizer: torch.optim.Optimizer,
    warmup_steps: int,
    total_steps: int,
    initial_lr: float,
    peak_lr: float,
    final_ratio: float = 0.5,
) -> LambdaLR:
    """Linear warmup → power-law decay scheduler."""
    alpha = np.log(1 / final_ratio) / np.log(total_steps / max(1, warmup_steps))

    def lr_lambda(step):
        if step < warmup_steps:
            return (initial_lr + (peak_lr - initial_lr) * step / max(1, warmup_steps)) / peak_lr
        return (warmup_steps / (step + 1)) ** alpha

    return LambdaLR(optimizer, lr_lambda)


def train_mdlm(
    model: nn.Module,
    train_dataloader: DataLoader,
    tokenizer: PreTrainedTokenizer,
    num_steps: int = 10000,
    lr: float = 5e-5,
    initial_lr: float = 0.0,
    device: str = 'cuda',
    activity_masking_prob: float = 0.1,
    activity_loss_weight: float = 1.0,
    warmup_steps: int = 0,
    scheduler_type: Optional[str] = None,
    final_lr_ratio: float = 0.5,
    log_every: int = 100,
    ema_decay: float = 0.999,
    use_ema: bool = True,
) -> Tuple[nn.Module, nn.Module]:
    """MDLM training loop. Returns (trained_model, ema_model)."""
    model = model.to(device)
    optimizer = AdamW(filter(lambda p: p.requires_grad, model.parameters()), lr=lr)

    ema = EMAModel(model, decay=ema_decay) if use_ema else None
    scheduler = get_modified_sqrt_decay_scheduler(
        optimizer, warmup_steps, num_steps, initial_lr, lr, final_lr_ratio
    ) if scheduler_type == 'modified_sqrt' else None

    mask_token_id = tokenizer.mask_token_id
    pad_token_id = tokenizer.pad_token_id

    model.train()
    train_iter = iter(train_dataloader)
    metrics = {'loss': 0, 'seq': 0, 'act': 0, 'seq_acc': 0, 'act_acc': 0,
               'masked': 0, 'total': 0, 'masked_act': 0, 'batch': 0}

    pbar = tqdm(range(1, num_steps + 1), desc="Training")
    for step in pbar:
        try:
            batch = next(train_iter)
        except StopIteration:
            train_iter = iter(train_dataloader)
            batch = next(train_iter)

        tokens = batch['input_ids'].to(device)
        species_ids = batch['species_ids'].to(device)
        activity = batch['activity_labels'].to(device)
        mask_vector = batch['masking_vector'].to(device)

        losses = train_step(
            model, tokens, activity, species_ids, mask_vector,
            mask_token_id, pad_token_id, activity_masking_prob, activity_loss_weight
        )

        optimizer.zero_grad()
        losses['loss'].backward()
        optimizer.step()

        if ema: ema.update(model)
        if scheduler: scheduler.step()

        # Track metrics
        metrics['loss'] += losses['loss'].item()
        metrics['seq'] += losses['seq_loss']
        metrics['act'] += losses['activity_loss']
        metrics['seq_acc'] += losses['seq_accuracy']
        metrics['act_acc'] += losses['act_accuracy'] * losses['masked_activity']
        metrics['masked'] += losses['masked_tokens']
        metrics['total'] += losses['total_tokens']
        metrics['masked_act'] += losses['masked_activity']
        metrics['batch'] += losses['batch_size']

        if step % log_every == 0:
            avg_act_acc = metrics['act_acc'] / max(1, metrics['masked_act'])
            tqdm.write(
                f"Step {step:5d} | loss: {metrics['loss']/log_every:.4f} | "
                f"seq_loss: {metrics['seq']/log_every:.4f} | seq_acc: {metrics['seq_acc']/log_every:.3f} | "
                f"act_loss: {metrics['act']/log_every:.4f} | act_acc: {avg_act_acc:.3f} | "
                f"lr: {optimizer.param_groups[0]['lr']:.2e}"
            )
            metrics = {k: 0 for k in metrics}

    return (model, ema.get_model()) if use_ema else (model, model)

## 4) 📊 Dataset

This section defines the PyTorch Dataset class for loading enhancer sequences.

---

### Dataset Structure

The `EnhancerDataset` class handles:
1. **Tokenization**: Convert DNA sequences to token IDs using the NTv3 tokenizer
2. **Activity labels**: Extract discrete activity bins (0-4)
3. **Masking vectors**: Create binary masks indicating which positions to train on

### Enhancer Insertion Positions

Different promoter types have the enhancer inserted at different positions:

| Promoter | Enhancer Start | Enhancer End | Length |
|----------|---------------|--------------|--------|
| DSCP | 1018 | 1267 | 249 bp |
| RpS12 | 968 | 1217 | 249 bp |

The `masking_vector` ensures we only apply MDLM loss to the enhancer region, not the flanking promoter/reporter sequences.

In [9]:
class EnhancerDataset(Dataset):
    """Dataset for enhancer generation training."""

    # Enhancer insertion positions for each promoter type
    PROMOTER_INSERTIONS = {
        'DSCP': [1018, 1267],
        'RpS12': [968, 1217],
    }

    def __init__(self, hf_dataset, tokenizer: PreTrainedTokenizer, species_dict: Dict[str, int]):
        self.data = hf_dataset
        self.tokenizer = tokenizer
        self.species_dict = species_dict

    def __len__(self) -> int:
        return len(self.data)

    def __getitem__(self, idx: int) -> Dict[str, Any]:
        item = self.data[idx]

        # Tokenize sequence
        tokens = self.tokenizer(
            item['full_sequence'], add_special_tokens=False, return_tensors='pt'
        )['input_ids'].squeeze(0)

        # Activity label (0-4)
        activity = torch.tensor(item.get('discrete_label', 0), dtype=torch.long)

        # Create masking vector for enhancer region only
        promoter_type = item.get('promoter')
        mask_interval = self.PROMOTER_INSERTIONS[promoter_type]
        masking_vector = torch.zeros(len(tokens), dtype=torch.bool)
        masking_vector[mask_interval[0]:mask_interval[1]] = True

        return {
            'input_ids': tokens,
            'species_ids': self.species_dict['drosophila_melanogaster'],
            'activity_labels': activity,
            'masking_vector': masking_vector
        }

## 5) 🚀 Run Training

Now we instantiate the dataset and run the training loop.

---

### Training Parameters

The configuration below is set for a **full training run**. For quick demo, decrease `num_steps` and adjust batch size according to your GPU memory:

In [ ]:
# Create dataset and dataloader
train_dataset = EnhancerDataset(dataset, tokenizer, generation_config.species_to_token_id)
train_loader = DataLoader(train_dataset, batch_size=32, shuffle=True, num_workers=0)

print(f"Training on {len(train_dataset)} samples")

Training on 804592 samples


### Understanding Training Metrics

During training, monitor these metrics:

| Metric | What to Watch |
|--------|---------------|
| `loss` | Total loss (seq + activity) | 
| `seq_loss` | Sequence prediction loss | 
| `seq_acc` | Token prediction accuracy | 
| `act_loss` | Activity prediction loss | 
| `act_acc` | Activity classification accuracy |

**Interpreting Results:**
- **seq_acc** measures how well the model predicts masked DNA tokens
- **act_acc** measures if the model learns the activity-sequence relationship

In [ ]:
# Train the model
device = 'cuda' if torch.cuda.is_available() else 'cpu'
print(f"Training on: {device}")

trained_model, ema_model = train_mdlm(
    model=generation_model,
    train_dataloader=train_loader,
    tokenizer=tokenizer,
    num_steps=500000,                    # Increase for real training (e.g., 50000)
    lr=1e-4,                        # Peak LR
    initial_lr=5e-5,                # Starting LR for warmup
    device=device,
    activity_masking_prob=0.1,      # 10% activity dropout for CFG
    activity_loss_weight=0.1,
    warmup_steps=25000,                 # Increase for real training
    scheduler_type='modified_sqrt',
    final_lr_ratio=0.5,
    log_every=2000,                    # Increase for real training (e.g., 1000)
    ema_decay=0.999,
    use_ema=True
)

# Use EMA model for generation (smoother, more stable)
generation_model = ema_model
print("Training complete!")

### Saving Checkpoints

After training, save both the training model and the EMA model. **Use the EMA model for generation** as it produces smoother, more stable outputs.

In [ ]:
#Save checkpoint
torch.save(trained_model.state_dict(), 'ntv3_generative_finetuned.pt')
torch.save(ema_model.state_dict(), 'ntv3_generative_finetuned_ema.pt')
print("Checkpoints saved!")